# Calculate OD

In [48]:
import os, sys, time, importlib
import osmnx

import geopandas as gpd
import pandas as pd
import networkx as nx
import numpy as np
sys.path.append("../../../GOSTnets")
import GOSTnets as gn

# pip install osmium
# import osmium, logging
# import shapely.wkb as wkblib

from shapely.geometry import LineString, Point

In [49]:
# This is a Jupyter Notebook extension which reloads all of the modules whenever you run the code
# This is optional but good if you are modifying and testing source code
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [50]:
from GOSTnets.load_traffic2 import *

In [51]:
#read_nodes = pd.read_csv('./vavuniya_unclean_nodes.csv')

In [52]:
#read_nodes[:5]

In [53]:
# read graph
G = nx.read_gpickle('./sri_lanka_unclean2_w_time_largest.pickle')

In [54]:
len(G.edges)

1675316

In [55]:
gn.example_edge(G, 5)

(1650104033, 6236632580, {'osm_id': 4860427, 'geometry': <shapely.geometry.linestring.LineString object at 0x7f9058e219d0>, 'infra_type': 'trunk', 'min_speed': 23.0, 'max_speed': 37.0, 'mean_speed': 26.793650793650794, 'length': 9.757789924575977, 'speed': 26.793650793650794, 'time': 1.3110585040840237, 'mode': 'drive'})
(1650104033, 970058024, {'osm_id': 152177791, 'geometry': <shapely.geometry.linestring.LineString object at 0x7f9058e21c90>, 'infra_type': 'trunk', 'min_speed': 23.0, 'max_speed': 37.0, 'mean_speed': 26.793650793650794, 'length': 16.0020254611234, 'speed': 26.793650793650794, 'time': 2.150035174515869, 'mode': 'drive'})
(6236632580, 6236632579, {'osm_id': 4860427, 'geometry': <shapely.geometry.linestring.LineString object at 0x7f9058e21d50>, 'infra_type': 'trunk', 'min_speed': 23.0, 'max_speed': 37.0, 'mean_speed': 26.793650793650794, 'length': 5.235256075996137, 'speed': 26.793650793650794, 'time': 0.7034099988364477, 'mode': 'drive'})
(6236632580, 1650104033, {'osm_i

## load origins

In [56]:
origins = gpd.read_file('./origins_destinations/cities_top10.shp')

In [57]:
origins

osm_id  code            fclass  population          name country  \
0    44240758  1001              city       27500  Nuwara Eliya     LKA   
1    50794342  1005  national_capital      753000       Colombo     LKA   
2   258049423  1001              city       40800        Matale     LKA   
3   330173100  1001              city       45400      Puttalam     LKA   
4   335253618  1001              city       99100   Trincomalee     LKA   
5  2050947471  1001              city      600000        Jaffna     LKA   
6  2908772560  1001              city      125000         Kandy     LKA   
7  3289447451  1001              city       20000       Gampaha     LKA   
8  3639539242  1001              city      110000        Matara     LKA   
9  3639546887  1001              city      120000         Galle     LKA   

                   geometry  
0  POINT (80.76707 6.97382)  
1  POINT (79.85385 6.93500)  
2  POINT (80.62342 7.47213)  
3  POINT (79.82866 8.03019)  
4  POINT (81.23450 8.57643)  
5  POINT (80.00930 9.66509)  
6  POINT (80.63508 7.29309)  
7  POINT (79.99514 7.09256)  
8  POINT (80.54829 5.94782)  
9  POINT (80.21495 6.03281)

## load destinations

In [58]:
destinations = gpd.read_file('./origins_destinations/tourism_w_cities_wgs84.shp')

In [59]:
destinations

Loc_name                                          LongLabel  \
0      World         Embekka Katharagama Dewalaya, Embekka, LKA   
1       None                                               None   
2      World  Royal Palace Park-Kandy, Keerthie Sri Rajasing...   
3      World                                         Kandy, LKA   
4      World  Bauddha Bala Mandalaya, Akkara Road, Ranawana ...   
..       ...                                                ...   
409    World      Wasana Trade Point, Temple Road, Negombo, LKA   
410    World  Post Office-Wadduwa, Wadduwa Station Road, Wad...   
411    World                    Madusanka, A8, Wekada West, LKA   
412    World  Post Office-Beruwala, Mangala Road, Paranakade...   
413    World            Garden Beach Hotel, Kalutara North, LKA   

                       ShortLabel Addr_type               Type  \
0    Embekka Katharagama Dewalaya       POI             Temple   
1                            None      None               None   
2         Royal Palace Park-Kandy       POI               Park   
3                           Kandy  Locality               City   
4          Bauddha Bala Mandalaya       POI             Temple   
..                            ...       ...                ...   
409            Wasana Trade Point       POI  Business Facility   
410           Post Office-Wadduwa       POI        Post Office   
411                     Madusanka       POI            Grocery   
412          Post Office-Beruwala       POI        Post Office   
413            Garden Beach Hotel       POI              Hotel   

                        PlaceName                              Place_addr  \
0    Embekka Katharagama Dewalaya                                 Embekka   
1                            None                                    None   
2         Royal Palace Park-Kandy  Keerthie Sri Rajasinghe Mawatha, Kandy   
3                           Kandy                                    None   
4          Bauddha Bala Mandalaya              Akkara Road, Ranawana East   
..                            ...                                     ...   
409            Wasana Trade Point                    Temple Road, Negombo   
410           Post Office-Wadduwa     Wadduwa Station Road, Wadduwa South   
411                     Madusanka                         A8, Wekada West   
412          Post Office-Beruwala                Mangala Road, Paranakade   
413            Garden Beach Hotel                          Kalutara North   

                              StAddr Block Sector  ... PostalExt Country  \
0                               None  None   None  ...      None     LKA   
1                               None  None   None  ...      None    None   
2    Keerthie Sri Rajasinghe Mawatha  None   None  ...      None     LKA   
3                               None  None   None  ...      None     LKA   
4                        Akkara Road  None   None  ...      None     LKA   
..                               ...   ...    ...  ...       ...     ...   
409                      Temple Road  None   None  ...      None     LKA   
410             Wadduwa Station Road  None   None  ...      None     LKA   
411                               A8  None   None  ...      None     LKA   
412                     Mangala Road  None   None  ...      None     LKA   
413                             None  None   None  ...      None     LKA   

    LangCode NEAR_FID     NEAR_DIST         NEAR_X         NEAR_Y nearCtyPop  \
0        ENG        7  11110.595704  459719.265399  806165.680488     125000   
1       None        3  15374.643812  458448.971316  825958.949979      40800   
2        ENG        7    482.167726  459719.265399  806165.680488     125000   
3        ENG        7    446.690670  459719.265399  806165.680488     125000   
4        ENG        7   4130.237703  459719.265399  806165.680488     125000   
..       ...      ...           ...            ...            ...        ...   
409     

In [60]:
origins_gdf = gn.pandana_snap_c(G, origins, source_crs = 'epsg:4326', target_crs = 'epsg:32644')

In [61]:
origins_gdf

osm_id  code            fclass  population          name country  \
0    44240758  1001              city       27500  Nuwara Eliya     LKA   
1    50794342  1005  national_capital      753000       Colombo     LKA   
2   258049423  1001              city       40800        Matale     LKA   
3   330173100  1001              city       45400      Puttalam     LKA   
4   335253618  1001              city       99100   Trincomalee     LKA   
5  2050947471  1001              city      600000        Jaffna     LKA   
6  2908772560  1001              city      125000         Kandy     LKA   
7  3289447451  1001              city       20000       Gampaha     LKA   
8  3639539242  1001              city      110000        Matara     LKA   
9  3639546887  1001              city      120000         Galle     LKA   

                   geometry          NN    NN_dist  
0  POINT (80.76707 6.97382)  4784044133   1.631987  
1  POINT (79.85385 6.93500)  5385270047   6.505032  
2  POINT (80.62342 7.47213)  1727494683  82.604133  
3  POINT (79.82866 8.03019)  4140985760   7.214712  
4  POINT (81.23450 8.57643)  1243386867   7.611852  
5  POINT (80.00930 9.66509)  7098642100   6.705113  
6  POINT (80.63508 7.29309)  4004620073  11.021930  
7  POINT (79.99514 7.09256)  3289453904  11.707473  
8  POINT (80.54829 5.94782)  1734550181  10.113321  
9  POINT (80.21495 6.03281)  3379679501   8.177613

In [62]:
origins_list = list(set(origins_gdf.NN))

In [63]:
destinations_gdf = gn.pandana_snap_c(G, destinations, source_crs = 'epsg:4326', target_crs = 'epsg:32644')

In [64]:
destinations_gdf

Loc_name                                          LongLabel  \
0      World         Embekka Katharagama Dewalaya, Embekka, LKA   
1       None                                               None   
2      World  Royal Palace Park-Kandy, Keerthie Sri Rajasing...   
3      World                                         Kandy, LKA   
4      World  Bauddha Bala Mandalaya, Akkara Road, Ranawana ...   
..       ...                                                ...   
409    World      Wasana Trade Point, Temple Road, Negombo, LKA   
410    World  Post Office-Wadduwa, Wadduwa Station Road, Wad...   
411    World                    Madusanka, A8, Wekada West, LKA   
412    World  Post Office-Beruwala, Mangala Road, Paranakade...   
413    World            Garden Beach Hotel, Kalutara North, LKA   

                       ShortLabel Addr_type               Type  \
0    Embekka Katharagama Dewalaya       POI             Temple   
1                            None      None               None   
2         Royal Palace Park-Kandy       POI               Park   
3                           Kandy  Locality               City   
4          Bauddha Bala Mandalaya       POI             Temple   
..                            ...       ...                ...   
409            Wasana Trade Point       POI  Business Facility   
410           Post Office-Wadduwa       POI        Post Office   
411                     Madusanka       POI            Grocery   
412          Post Office-Beruwala       POI        Post Office   
413            Garden Beach Hotel       POI              Hotel   

                        PlaceName                              Place_addr  \
0    Embekka Katharagama Dewalaya                                 Embekka   
1                            None                                    None   
2         Royal Palace Park-Kandy  Keerthie Sri Rajasinghe Mawatha, Kandy   
3                           Kandy                                    None   
4          Bauddha Bala Mandalaya              Akkara Road, Ranawana East   
..                            ...                                     ...   
409            Wasana Trade Point                    Temple Road, Negombo   
410           Post Office-Wadduwa     Wadduwa Station Road, Wadduwa South   
411                     Madusanka                         A8, Wekada West   
412          Post Office-Beruwala                Mangala Road, Paranakade   
413            Garden Beach Hotel                          Kalutara North   

                              StAddr Block Sector  ... LangCode NEAR_FID  \
0                               None  None   None  ...      ENG        7   
1                               None  None   None  ...     None        3   
2    Keerthie Sri Rajasinghe Mawatha  None   None  ...      ENG        7   
3                               None  None   None  ...      ENG        7   
4                        Akkara Road  None   None  ...      ENG        7   
..                               ...   ...    ...  ...      ...      ...   
409                      Temple Road  None   None  ...      ENG        8   
410             Wadduwa Station Road  None   None  ...      ENG        2   
411                               A8  None   None  ...      ENG        2   
412                     Mangala Road  None   None  ...      ENG        2   
413                             None  None   None  ...      ENG        2   

        NEAR_DIST         NEAR_X         NEAR_Y nearCtyPop     name  \
0    11110.595704  459719.265399  806165.680488     125000    Kandy   
1    15374.643812  458448.971316  825958.949979      40800   Matale   
2      482.167726  459719.265399  806165.680488     125000    Kandy   
3      446.690670  459719.265399  806165.680488     125000    Kandy   
4     4130.237703  459719.265399  806165.680488     125000    Kandy   
..            ...            ...            ...        ...      ...   
409  18946.453259  389028.597467  784101.180029      20000  Gampaha   


In [65]:
destinations_list = list(set(destinations_gdf.NN))

In [66]:
destinations_list

[2291208197,
 1667080206,
 6991570964,
 6117715989,
 1743126554,
 2100457519,
 1185558575,
 130445367,
 2085208123,
 4047450172,
 1242787912,
 1691609164,
 4891658323,
 4893239380,
 1517451347,
 3799898203,
 2094557278,
 7066196064,
 3587975265,
 2078574693,
 1745895527,
 1741201515,
 3249014896,
 4784988278,
 1895649399,
 3208652929,
 610939019,
 3800084623,
 666892434,
 1242787995,
 308865188,
 3806787750,
 4248172715,
 47823021,
 1146790064,
 5580828849,
 4600967349,
 3902560439,
 3081279676,
 5497589950,
 2342916291,
 3985412306,
 1709670615,
 1722822882,
 3851290872,
 6988599546,
 1924788477,
 7083442431,
 61802753,
 5596123398,
 4111669517,
 3804238095,
 2833357077,
 2634987798,
 5504295192,
 5997193508,
 3686420776,
 4579338537,
 4007776558,
 3803965753,
 6181355836,
 1269985600,
 2145161538,
 3213648201,
 2079873354,
 1952715084,
 849219917,
 4217581902,
 2151514445,
 5265641820,
 2902126951,
 5874008423,
 1974698347,
 3169970562,
 1896380803,
 5216672133,
 7350159754,
 2087539

## Calculate OD

In [67]:
# It will use the default weight of 'time'
import time

start = time.time()

OD = gn.calculate_OD(G, origins_list, destinations_list, fail_value = 9999999)

end = time.time()
print(end - start)

64.2102222442627


In [68]:
OD

array([[18510.07439113, 12507.29594792, 10194.32685517, ...,
         4829.20915756, 18447.90111899, 10138.05719571],
       [18168.79048334, 16420.96031958, 15970.77124844, ...,
        17919.4150786 , 17941.59963555, 15914.50158898],
       [22253.89341784,  5577.87119714,  7919.8878946 , ...,
        19234.27084502, 22026.70257005,  8107.09245389],
       ...,
       [23877.89053379, 28003.1856312 , 26374.80525088, ...,
        12465.60768133, 23815.71726166, 26318.53559141],
       [13600.79878917, 13830.61934095, 12441.78656499, ...,
         8611.52067083, 13538.62551703, 12385.51690552],
       [22760.36981733,  4335.42794116,   527.0371602 , ...,
        13976.55410784, 22698.19654519,   257.35757222]])

In [69]:
OD_df = pd.DataFrame(OD, index = origins_list, columns = destinations_list)

In [70]:
OD_df

2291208197    1667080206    6991570964    6117715989  \
4140985760  18510.074391  12507.295948  10194.326855  17017.046783   
4784044133  18168.790483  16420.960320  15970.771248    246.884367   
1734550181  22253.893418   5577.871197   7919.887895  15703.435161   
4004620073  15357.120897  12269.390354  10880.557578   7577.372332   
3379679501  23632.568454   4604.393388   6946.410085  17082.110198   
3289453904  20834.449315   4373.582498   2984.749722  13897.581977   
1243386867  10050.216305  21028.939802  19640.107026  21176.982762   
7098642100  23877.890534  28003.185631  26374.805251  29229.796481   
1727494683  13600.798789  13830.619341  12441.786565   9922.327601   
5385270047  22760.369817   4335.427941    527.037160  15823.502479   

              1743126554    2100457519    1185558575    130445367   \
4140985760  11058.179415  14588.843982  11616.506298  14153.017294   
4784044133   8132.610523  26436.198542  16370.683271  18429.611369   
1734550181  15053.684958  28808.955754   6628.789813   4084.405129   
4004620073   2363.735176  19278.819754  11542.389592  13915.111700   
3379679501  14080.207149  27835.477944   5655.312004   2641.929211   
3289453904   8109.595324  21754.640756   3646.581736   6019.303844   
1243386867  15603.274375   7627.850486  20301.939039  22674.661147   
7098642100  23656.088094   9325.359153  27276.184869  29648.906977   
1727494683   4401.428912  16760.416039  13103.618578  15476.340687   
5385270047  10035.515826  23551.239017   2070.903425   6179.747102   

              2085208123    4047450172  ...    3772792789    3772792790  \
4140985760  21992.550175   9847.193878  ...  10785.029235  10774.574424   
4784044133  10032.738931   7421.909044  ...  16542.592663  16551.018817   
1734550181  12451.921281  15797.568395  ...   7155.992360   7166.447171   
4004620073  16917.251506    175.355078  ...  11471.259958  11460.805147   
3379679501  13830.596317  14824.090585  ...   6182.514551   6192.969362   
3289453904  14196.753964   8853.478760  ...   3575.452102   3564.997291   
1243386867  25899.034561  13597.703797  ...  20230.809405  20220.354595   
7098642100  34941.923384  21650.517516  ...  26965.507630  26955.052820   
1727494683  19262.206776   2343.048636  ...  13032.488944  13022.034134   
5385270047  15114.659932  10779.399262  ...   1389.961431   1379.506621   

              1730404311    258523099     6564888541    3216934896  \
4140985760  20191.061674  11498.594777  12598.994605  12013.650506   
4784044133  12617.043637  15568.322303  24446.349165   9460.677768   
1734550181   5608.141428  20767.059336  26819.106377  11771.937683   
4004620073  17386.911484   9107.722890  17288.970377   7586.305618   
3379679501   6986.816464  19793.581527  25845.628567  10798.459874   
3289453904  12057.348224  13822.969702  19764.791379   5474.782889   
1243386867  24473.158962   6771.671943  10369.806621  17918.607278   
7098642100  33516.047784  17718.037277   5435.996178  25167.001175   
1727494683  18380.281612   6589.319175  14770.566663   9819.827132   
5385270047  12217.791482  15748.890204  21561.389640   7361.264357   

              1506164725    1657419767    1675585534    4621961215  
4140985760  15059.136708   4829.209158  18447.901119  10138.057196  
4784044133  17173.575547  17919.415079  17941.599636  15914.501589  
1734550181   2828.369308  19234.270845  22026.702570   8107.092454  
4004620073  14821.231114  11054.161876  15129.930049  10824.287919  
3379679501    248.574822  18260.793036  23405.377606   7133.614644  
3289453904   6925.423258  12179.955848  20772.276043   2928.480063  
1243386867  23580.780562   7247.822892   9988.043033  19583.837366  
7098642100  30555.026391  12465.607681  23815.717262  26318.535591  
1727494683  16382.460101   8611.520671  13538.625517  12385.516906  
5385270047   7085.866516  13976.554108  22698.196545    257.357572  

[10 rows x 337 columns]

In [71]:
#OD_df.min(axis=0)

In [72]:
# first column is the destination (tourist point), and the second column is the nearest city
OD_df.idxmin(axis=0)

2291208197    1243386867
1667080206    5385270047
6991570964    5385270047
6117715989    4784044133
1743126554    4004620073
                 ...    
3216934896    3289453904
1506164725    3379679501
1657419767    4140985760
1675585534    1243386867
4621961215    5385270047
Length: 337, dtype: int64

In [73]:
#OD_df.idxmin(axis=0).to_frame(0)

In [74]:
# takes the min index value of each column, then groups by the first index (0) and takes the first entry
groupby_obj = OD_df.idxmin(axis=0).to_frame(0).groupby(0)[0]

In [75]:
groupby_obj

In [76]:
groupby_obj.apply(list)

0
1243386867    [1243386867, 1243386867, 1243386867, 124338686...
1727494683    [1727494683, 1727494683, 1727494683, 172749468...
1734550181    [1734550181, 1734550181, 1734550181, 173455018...
3289453904    [3289453904, 3289453904, 3289453904, 328945390...
3379679501    [3379679501, 3379679501, 3379679501, 337967950...
4004620073    [4004620073, 4004620073, 4004620073, 400462007...
4140985760    [4140985760, 4140985760, 4140985760, 414098576...
4784044133    [4784044133, 4784044133, 4784044133, 478404413...
5385270047    [5385270047, 5385270047, 5385270047, 538527004...
7098642100    [7098642100, 7098642100, 7098642100, 709864210...
Name: 0, dtype: object

In [77]:
type(groupby_obj.apply(list))

pandas.core.series.Series

In [78]:
dict_ex = groupby_obj.apply(list).to_dict()

In [79]:
dict_ex

{1243386867: [1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867,
  1243386867],
 1727494683: [1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494683,
  1727494

In [80]:
city_tourist_pt_dict = {}
for name, group in groupby_obj:
    #print(group)
    for items in group.iteritems(): 
        print(items[1])
        if items[1] not in city_tourist_pt_dict:
            city_tourist_pt_dict[items[1]] = [items[0]]
        else:
            #append value to list in dict value
            city_tourist_pt_dict[items[1]].append(items[0])
    #print(type(group))
    #print(group.head(1))

    #print(name)
    #print(city_tourist_pt_dict[group])

1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1243386867
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1727494683
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181
1734550181

In [81]:
city_tourist_pt_dict

{1243386867: [2291208197,
  2100457519,
  1242787912,
  1895649399,
  1242787995,
  3806787750,
  4248172715,
  5580828849,
  3851290872,
  4579338537,
  1896380803,
  1884656092,
  1896380948,
  1880627748,
  6177931854,
  7076053840,
  3985464364,
  4542639194,
  4376980578,
  3805734132,
  3315891502,
  2278210866,
  3893372372,
  7025200613,
  2341660185,
  6021684779,
  1676588668,
  3350242971,
  1685802748,
  1723379544,
  2477387622,
  1775835028,
  3165939618,
  5965445027,
  1675585459,
  1675585534],
 1727494683: [4784988278,
  3208652929,
  6988599546,
  2833357077,
  6181355836,
  3213648201,
  2646372818,
  5441882639,
  5035668064,
  2051261052,
  2279244515,
  1692965634,
  2831541077,
  3748668362,
  3218396149,
  1241535503,
  4924478499,
  1241527387,
  5644231795,
  1241527444,
  258057398,
  3280149722,
  1241527517,
  2833347872,
  2821176699,
  5483879958,
  2297833003,
  3218405040,
  1241534200,
  2303446810,
  3999442747,
  2799732582,
  2799732584,
  34724535

In [82]:
groupby_obj.describe()

count          mean  std           min           25%  \
0                                                                  
1243386867   36.0  1.243387e+09  0.0  1.243387e+09  1.243387e+09   
1727494683   35.0  1.727495e+09  0.0  1.727495e+09  1.727495e+09   
1734550181   39.0  1.734550e+09  0.0  1.734550e+09  1.734550e+09   
3289453904   15.0  3.289454e+09  0.0  3.289454e+09  3.289454e+09   
3379679501   29.0  3.379680e+09  0.0  3.379680e+09  3.379680e+09   
4004620073   43.0  4.004620e+09  0.0  4.004620e+09  4.004620e+09   
4140985760   36.0  4.140986e+09  0.0  4.140986e+09  4.140986e+09   
4784044133   35.0  4.784044e+09  0.0  4.784044e+09  4.784044e+09   
5385270047   51.0  5.385270e+09  0.0  5.385270e+09  5.385270e+09   
7098642100   18.0  7.098642e+09  0.0  7.098642e+09  7.098642e+09   

                     50%           75%           max  
0                                                     
1243386867  1.243387e+09  1.243387e+09  1.243387e+09  
1727494683  1.727495e+09  1.727495e+09  1.727495e+09  
1734550181  1.734550e+09  1.734550e+09  1.734550e+09  
3289453904  3.289454e+09  3.289454e+09  3.289454e+09  
3379679501  3.379680e+09  3.379680e+09  3.379680e+09  
4004620073  4.004620e+09  4.004620e+09  4.004620e+09  
4140985760  4.140986e+09  4.140986e+09  4.140986e+09  
4784044133  4.784044e+09  4.784044e+09  4.784044e+09  
5385270047  5.385270e+09  5.385270e+09  5.385270e+09  
7098642100  7.098642e+09  7.098642e+09  7.098642e+09

## Loop through dictionary in order to do a calculate_OD for each city's nearest tourist sites

In [83]:
OD = {}
OD_df = {}
for city,tourist_pts in city_tourist_pt_dict.items():
    OD[city] = gn.calculate_OD(G, [city], tourist_pts, fail_value = 9999999)
    OD_df[city] = pd.DataFrame(OD[city], index = [city], columns = tourist_pts)

In [84]:
sample_df = OD_df[4784044133]
sample_df

6117715989    2085208123   2078574693   1146790064   5497589950  \
4784044133  246.884367  10032.738931  5795.916461  5595.063132  2950.074792   

             1709670615  7083442431  5596123398   3686420776   849219917   \
4784044133  7434.484289  487.724105  108.423476  1637.208436  1904.107684   

            ...  4342594760   3301905899  198553180    2408066657  \
4784044133  ...  3726.12794  5532.948146  432.959124  1479.318821   

             3615147754   1713880855   5497589553   2057039735   2057039753  \
4784044133  8967.031034  5902.910295  2800.297799  5480.234495  5469.468574   

            77682630    
4784044133   25.618408  

[1 rows x 35 columns]

### time calculateOD time for one city and it's set of tourist points

In [85]:
start = time.time()
OD[4784044133] = gn.calculate_OD(G, [4784044133], tourist_pts, fail_value = 9999999)
print(time.time() - start)

6.08395791053772


In [160]:
OD[4784044133][0].sum()

198129.8004423761

### ver 1 of heuristic

In [86]:
gn.example_edge(G,2)

(1650104033, 6236632580, {'osm_id': 4860427, 'geometry': <shapely.geometry.linestring.LineString object at 0x7f9058e219d0>, 'infra_type': 'trunk', 'min_speed': 23.0, 'max_speed': 37.0, 'mean_speed': 26.793650793650794, 'length': 9.757789924575977, 'speed': 26.793650793650794, 'time': 1.3110585040840237, 'mode': 'drive'})
(1650104033, 970058024, {'osm_id': 152177791, 'geometry': <shapely.geometry.linestring.LineString object at 0x7f9058e21c90>, 'infra_type': 'trunk', 'min_speed': 23.0, 'max_speed': 37.0, 'mean_speed': 26.793650793650794, 'length': 16.0020254611234, 'speed': 26.793650793650794, 'time': 2.150035174515869, 'mode': 'drive'})


In [143]:
# loop through graph edges
    # if edge is not secondary or less, then calculate the time saved attribute
        # time saved is length / 2.77 (in sec), this assumes that a road improvement will result in 10km/hr speed improvement
        # assign an improvement cost
    # else:
        # assign a time saved of 0
        # assign a very high improvement cost
    
for u, v, data in G.edges(data=True):

        rural_roads_list = ['residential','secondary','secondary_link','tertiary','tertiary_link','unclassified']

        if data['infra_type'] in rural_roads_list:
            new_time = (data['speed'] + 10) * 1000 / 3600
            data['sec_saved'] = data['length'] / new_time
            data['improvement_cost'] = 174861 * data['length'] / 1000
        else:
            data['sec_saved'] = 0
            # very high number
            data['improvement_cost'] = 10000000000


In [144]:
gn.example_edge(G,25)

(1650104033, 6236632580, {'osm_id': 4860427, 'geometry': <shapely.geometry.linestring.LineString object at 0x7f9058e219d0>, 'infra_type': 'trunk', 'min_speed': 23.0, 'max_speed': 37.0, 'mean_speed': 26.793650793650794, 'length': 9.757789924575977, 'speed': 26.793650793650794, 'time': 1.3110585040840237, 'mode': 'drive', 'sec_saved': 0, 'improvement_cost': 10000000000})
(1650104033, 970058024, {'osm_id': 152177791, 'geometry': <shapely.geometry.linestring.LineString object at 0x7f9058e21c90>, 'infra_type': 'trunk', 'min_speed': 23.0, 'max_speed': 37.0, 'mean_speed': 26.793650793650794, 'length': 16.0020254611234, 'speed': 26.793650793650794, 'time': 2.150035174515869, 'mode': 'drive', 'sec_saved': 0, 'improvement_cost': 10000000000})
(6236632580, 6236632579, {'osm_id': 4860427, 'geometry': <shapely.geometry.linestring.LineString object at 0x7f9058e21d50>, 'infra_type': 'trunk', 'min_speed': 23.0, 'max_speed': 37.0, 'mean_speed': 26.793650793650794, 'length': 5.235256075996137, 'speed': 

In [145]:
# testing
import random
#G=nx.Graph()
#G.add_edges_from([[1,2],[1,3],[2,3],[2,4],[3,5],[4,5]])
random_edges=random.sample(list(G.edges()),k=1)
#G.remove_edges_from(to_remove)
#print(G.edges())
print(random_edges)

[(102757363, 5210894893)]


In [146]:
# This is too slow, instead maybe re-order list randomly and pick in order.
list(G.edges())

[(1650104033, 6236632580),
 (1650104033, 970058024),
 (6236632580, 6236632579),
 (6236632580, 1650104033),
 (6236632579, 6236632578),
 (6236632579, 6236632580),
 (6236632578, 6236632577),
 (6236632578, 6236632579),
 (6236632578, 6236632550),
 (6236632577, 6236632576),
 (6236632577, 6236632578),
 (6236632576, 6236632575),
 (6236632576, 6236632577),
 (6236632575, 6236632574),
 (6236632575, 6236632549),
 (6236632575, 6236632576),
 (6236632574, 6236632573),
 (6236632574, 6236632575),
 (6236632573, 6236632572),
 (6236632573, 6236632574),
 (6236632572, 4689100340),
 (6236632572, 6236632573),
 (4689100340, 4689100341),
 (4689100340, 6236632572),
 (4689100341, 3662706646),
 (4689100341, 4689100340),
 (3662706646, 3594147916),
 (3662706646, 4689100341),
 (3594147916, 3697151657),
 (3594147916, 3662706646),
 (3594147916, 3697145064),
 (31363742, 31363743),
 (31363742, 48299383),
 (31363742, 5379797719),
 (31363743, 5379799622),
 (31363743, 31363742),
 (5379799622, 3726382944),
 (5379799622, 5379

In [147]:
random_edge_list = list(G.edges())

In [148]:
len(random_edge_list)

1675316

In [149]:
random_edge_list = random.sample(random_edge_list, len(random_edge_list))

In [150]:
print(random_edge_list[:10])

[(3819995223, 4784044121), (4524889468, 4524889469), (4897352631, 4897352630), (2132088282, 2132088409), (3960756078, 3960756077), (3991524077, 3991524076), (4464348978, 3088885766), (4489688118, 4489688129), (5326985165, 5326985164), (3569068224, 4781136851)]


In [151]:
G.get_edge_data(random_edges[0][0], random_edges[0][1])[0]['length']/1000

0.0266913653789088

In [152]:
# to calculate budget the study areas cross admin1 areas, which are which the budget is based
# Therefore for now, just use 1 budget limit number for country 300km, and divide per 10 city areas, so 30km per city

In [153]:
# randomly pick initial solution by randomly picking edges as long as below budget
max_km = 30
total_km = 0

initial_solution = []

for item in random_edge_list:
    random_edge = item
    print(random_edge)
    random_edge_km = G.get_edge_data(random_edge[0], random_edge[1])[0]['length'] / 1000
    if total_km + random_edge_km < max_km:
        initial_solution.append([random_edge[0], random_edge[1]])
        total_km += random_edge_km
        print('total_km')
        print(total_km)
    else:
        break

# initial solution = list of improved edges
# ex. initial_solution = [[node_id1, node_id2],[node_id2, node_id3], [node_id7, node_id12]]

(3819995223, 4784044121)
total_km
0.0012657827326505158
(4524889468, 4524889469)
total_km
0.023827440029559114
(4897352631, 4897352630)
total_km
0.05740372737943461
(2132088282, 2132088409)
total_km
0.2103952487366703
(3960756078, 3960756077)
total_km
0.23387604983214094
(3991524077, 3991524076)
total_km
0.2522308117119498
(4464348978, 3088885766)
total_km
0.27353418350675024
(4489688118, 4489688129)
total_km
0.43697096956566883
(5326985165, 5326985164)
total_km
0.48025614755538976
(3569068224, 4781136851)
total_km
0.912966353071528
(2074229712, 3237687698)
total_km
0.9416687390293689
(2686078362, 2686078363)
total_km
0.9500900251844612
(3508112156, 3508112155)
total_km
0.9664115510263488
(5229820720, 5229820721)
total_km
0.9722764903835583
(1223898800, 1223898753)
total_km
1.0168541848899155
(3587979680, 3587979672)
total_km
1.0382065524199324
(4136176172, 4136176171)
total_km
1.043424711674864
(3963763124, 3963763125)
total_km
1.071851272730982
(2154098369, 2154098203)
total_km
1.100

(2365902876, 1268340416)
total_km
25.155684312988914
(6734493435, 6734493434)
total_km
25.198116527942826
(2304485529, 2304485517)
total_km
25.247075971363756
(3712020320, 311128416)
total_km
25.439941205699775
(4036017556, 4047457063)
total_km
25.44672503321113
(3289433970, 3289433730)
total_km
25.459991876862823
(5573648474, 5573648475)
total_km
25.523755284567134
(3622798733, 3622790689)
total_km
25.541476080418263
(2031628032, 2031627995)
total_km
25.575926084695947
(2081239326, 2081239323)
total_km
25.618328375533938
(5236002329, 5590605621)
total_km
25.622319918604333
(6957433330, 6957433329)
total_km
25.63904531981703
(4893731305, 4893731306)
total_km
25.649380885655166
(5968248577, 445280939)
total_km
25.656914777421647
(2353105194, 2190788366)
total_km
25.688501686081096
(3313366419, 3313366376)
total_km
25.740723423347703
(3377606372, 6247740238)
total_km
25.767551787307433
(3658679399, 3658679400)
total_km
25.830905284992692
(3522179263, 3522179710)
total_km
25.8493269793957

In [154]:
len(initial_solution)

496

In [155]:
# modify G with time saved
G_time_saved = G.copy()

for u, v, data in G_time_saved.edges(data=True):
    data['permutation_time'] = data['time'] - data['sec_saved']

In [156]:
# evaluate initial solution
OD[4784044133] = gn.calculate_OD(G_time_saved, [4784044133], tourist_pts, fail_value = 9999999, weight = 'permutation_time')

In [159]:
# calculate total time
OD[4784044133][0].sum()

198129.8004423761

In [108]:
# old slow code:
# randomly pick initial solution by randomly picking edges as long as below budget
max_km = 30
total_km = 0

initial_solution = []

condition = True
while condition:
    random_edge = random.sample(list(G.edges()),k=1)
    random_edge_km = G.get_edge_data(random_edges[0][0], random_edges[0][1])[0]['length'] / 1000
    if total_km + random_edge_km < max_km:
        initial_solution.append([random_edges[0][0], random_edges[0][1]])
        total_km += random_edge_km
        print('total_km')
        print(total_km)
    else:
        condition = False
# initial solution = list of improved edges
# ex. initial_solution = [[node_id1, node_id2],[node_id2, node_id3], [node_id7, node_id12]]

total_km
0.009609953245512995
total_km
0.01921990649102599
total_km
0.028829859736538982
total_km
0.03843981298205198
total_km
0.048049766227564975


KeyboardInterrupt: 

In [ ]:
initial_solution

In [ ]:
len(initial_solution)

In [ ]:
# move
# randomly pick and edge to interchange, interchange that edge by: randomly picking edges from graph until budget is met

## Now work on generating routes and visualizing them

In [ ]:
#to node
#4784044133
#from node
#3819995230

In [ ]:
gn.example_edge(G,2)

In [ ]:
G.edges([1650104033,6236632580])

In [ ]:
G.edges([1650104033, 970058024])

In [ ]:
G.edges([4784044133,3819995230])

In [ ]:
G.get_edge_data(4784044133, 3819995230)

In [ ]:
G.get_edge_data(4784044133, 3819995230)[0]['geometry'].coords

In [ ]:
from shapely.ops import linemerge
#linemerge(lines)

In [48]:
def tabulate_edges(route):
    edge_table = []
    route_geometry = LineString()
    for idx in range(0, len(route) - 1):
        edge_table.append([route[idx], route[idx+1]])
        # look up line
        #print('to node')
        #print(route[idx])
        #print('from node')
        #print(route[idx+1])
        edge_geometry = G.get_edge_data(route[idx],route[idx+1])[0]['geometry']
        route_geometry = route_geometry.union(edge_geometry)
    print('print route_geometry')
    print(route_geometry)
    
    return(edge_table, route_geometry)

In [49]:
#complete_routes = gpd.GeoDataFrame(columns=['o', 'd', 'geometry'])

In [50]:
#complete_routes

In [80]:
from itertools import islice
LIMIT = 10000

    
complete_edges = []
complete_routes = []


count = 0

# This will iterate through all of the values in the OD Matrix, therefore you will see edge being counted 
# in both directions, for example if there is an edge of node 1 to node 2, then there will be an edge 
# corresponding to of node 2 to node 1

# for origin, row in sample_df.iterrows(): 
for origin, row in islice(sample_df.iterrows(), LIMIT):    
    for destination, value in islice(row.items(), LIMIT):
        try:
            origin = int(origin)
        except:
            pass
        try:
            destination = int(destination)
        except:
            pass
        
        count = count + 1
        
        route = nx.dijkstra_path(G, origin, destination, weight = 'time')
        #path_edges = zip(route,route[1:])
        #print('print path_edges')
        #print(list(path_edges))
        # print(route)
        edge_table, route_geometry = tabulate_edges(route)
        print('print edge_table:')
        print(edge_table)
        complete_edges = complete_edges + edge_table
        #print('route_time')
        #print(value)
        complete_routes.append([edge_table[0][0], edge_table[-1][1], value, route_geometry])
        print('edge_table[:-1]')
        print(edge_table[-1][1])

print route_geometry
MULTILINESTRING ((80.7670837 6.9738216, 80.76707500000001 6.9738283), (80.7670928 6.9738167, 80.7670837 6.9738216), (80.7670928 6.9738167, 80.7670457 6.973783), (80.7670457 6.973783, 80.7670078 6.9737515), (80.7670078 6.9737515, 80.7669736 6.9737191), (80.7669736 6.9737191, 80.7669571 6.9736939), (80.7669571 6.9736939, 80.7669453 6.9736601), (80.7669453 6.9736601, 80.76693400000001 6.973613), (80.76693400000001 6.973613, 80.7669259 6.9735561), (80.7669259 6.9735561, 80.7669059 6.9733364), (80.7669059 6.9733364, 80.76686189999999 6.9727634), (80.766161 6.9732913, 80.766249 6.9730985, 80.7663088 6.9730028, 80.7663728 6.9729042, 80.7664632 6.9727654, 80.7664728 6.9727505, 80.7664824 6.9727385, 80.7664946 6.9727306, 80.7665136 6.9727272, 80.7665373 6.9727275, 80.76686189999999 6.9727634), (80.7660403 6.9732288, 80.766161 6.9732913), (80.7659816 6.9731976, 80.7660403 6.9732288), (80.7659352 6.9731663, 80.7659816 6.9731976), (80.7658029 6.9730515, 80.7659352 6.9731663), 

print route_geometry
MULTILINESTRING ((80.7670837 6.9738216, 80.76707500000001 6.9738283), (80.7670928 6.9738167, 80.7670837 6.9738216), (80.7670928 6.9738167, 80.7670457 6.973783), (80.7670457 6.973783, 80.7670078 6.9737515), (80.7670078 6.9737515, 80.7669736 6.9737191), (80.7669736 6.9737191, 80.7669571 6.9736939), (80.7669571 6.9736939, 80.7669453 6.9736601), (80.7669453 6.9736601, 80.76693400000001 6.973613), (80.76693400000001 6.973613, 80.7669259 6.9735561), (80.7669259 6.9735561, 80.7669059 6.9733364), (80.7669059 6.9733364, 80.76686189999999 6.9727634), (80.76686189999999 6.9727634, 80.7668595 6.9726027), (80.7668595 6.9726027, 80.766862 6.9724381), (80.766862 6.9724381, 80.7668706 6.9721991), (80.7668706 6.9721991, 80.7668843 6.9720105), (80.7668843 6.9720105, 80.76690000000001 6.9717953), (80.76690000000001 6.9717953, 80.7669267 6.9717803), (80.7669267 6.9717803, 80.766947 6.9717576), (80.766947 6.9717576, 80.7669587 6.9717295), (80.7669587 6.9717295, 80.7669606 6.9716991), (

print route_geometry
MULTILINESTRING ((80.7670837 6.9738216, 80.76707500000001 6.9738283), (80.7670928 6.9738167, 80.7670837 6.9738216), (80.7670928 6.9738167, 80.7670457 6.973783), (80.7670457 6.973783, 80.7670078 6.9737515), (80.7670078 6.9737515, 80.7669736 6.9737191), (80.7669736 6.9737191, 80.7669571 6.9736939), (80.7669571 6.9736939, 80.7669453 6.9736601), (80.7669453 6.9736601, 80.76693400000001 6.973613), (80.76693400000001 6.973613, 80.7669259 6.9735561), (80.7669259 6.9735561, 80.7669059 6.9733364), (80.7669059 6.9733364, 80.76686189999999 6.9727634), (80.76686189999999 6.9727634, 80.7668595 6.9726027), (80.7668595 6.9726027, 80.766862 6.9724381), (80.766862 6.9724381, 80.7668706 6.9721991), (80.7668706 6.9721991, 80.7668843 6.9720105), (80.7668843 6.9720105, 80.76690000000001 6.9717953), (80.76690000000001 6.9717953, 80.7669267 6.9717803), (80.7669267 6.9717803, 80.766947 6.9717576), (80.766947 6.9717576, 80.7669587 6.9717295), (80.7669587 6.9717295, 80.7669606 6.9716991), (

print route_geometry
MULTILINESTRING ((80.7670837 6.9738216, 80.76707500000001 6.9738283), (80.7670928 6.9738167, 80.7670837 6.9738216), (80.7670928 6.9738167, 80.7670457 6.973783), (80.7670457 6.973783, 80.7670078 6.9737515), (80.7670078 6.9737515, 80.7669736 6.9737191), (80.7669736 6.9737191, 80.7669571 6.9736939), (80.7669571 6.9736939, 80.7669453 6.9736601), (80.7669453 6.9736601, 80.76693400000001 6.973613), (80.76693400000001 6.973613, 80.7669259 6.9735561), (80.7669259 6.9735561, 80.7669059 6.9733364), (80.7669059 6.9733364, 80.76686189999999 6.9727634), (80.76686189999999 6.9727634, 80.7668595 6.9726027), (80.7668595 6.9726027, 80.766862 6.9724381), (80.766862 6.9724381, 80.7668706 6.9721991), (80.7668706 6.9721991, 80.7668843 6.9720105), (80.7668843 6.9720105, 80.76690000000001 6.9717953), (80.76690000000001 6.9717953, 80.7669267 6.9717803), (80.7669267 6.9717803, 80.766947 6.9717576), (80.766947 6.9717576, 80.7669587 6.9717295), (80.7669587 6.9717295, 80.7669606 6.9716991), (

print route_geometry
MULTILINESTRING ((80.7670837 6.9738216, 80.76707500000001 6.9738283), (80.7670928 6.9738167, 80.7670837 6.9738216), (80.7670928 6.9738167, 80.7670457 6.973783), (80.7670457 6.973783, 80.7670078 6.9737515), (80.7670078 6.9737515, 80.7669736 6.9737191), (80.7669736 6.9737191, 80.7669571 6.9736939), (80.7669571 6.9736939, 80.7669453 6.9736601), (80.7669453 6.9736601, 80.76693400000001 6.973613), (80.76693400000001 6.973613, 80.7669259 6.9735561), (80.7669259 6.9735561, 80.7669059 6.9733364), (80.7669059 6.9733364, 80.76686189999999 6.9727634), (80.76686189999999 6.9727634, 80.7668595 6.9726027), (80.7668595 6.9726027, 80.766862 6.9724381), (80.766862 6.9724381, 80.7668706 6.9721991), (80.7668706 6.9721991, 80.7668843 6.9720105), (80.7668843 6.9720105, 80.76690000000001 6.9717953), (80.76690000000001 6.9717953, 80.7669267 6.9717803), (80.7669267 6.9717803, 80.766947 6.9717576), (80.766947 6.9717576, 80.7669587 6.9717295), (80.7669587 6.9717295, 80.7669606 6.9716991), (

...

print route_geometry
MULTILINESTRING ((80.7670837 6.9738216, 80.76707500000001 6.9738283), (80.7670928 6.9738167, 80.7670837 6.9738216), (80.7670928 6.9738167, 80.7670457 6.973783), (80.7670457 6.973783, 80.7670078 6.9737515), (80.7670078 6.9737515, 80.7669736 6.9737191), (80.7669736 6.9737191, 80.7669571 6.9736939), (80.7669571 6.9736939, 80.7669453 6.9736601), (80.7669453 6.9736601, 80.76693400000001 6.973613), (80.76693400000001 6.973613, 80.7669259 6.9735561), (80.7669259 6.9735561, 80.7669059 6.9733364), (80.7669059 6.9733364, 80.76686189999999 6.9727634), (80.76686189999999 6.9727634, 80.7668595 6.9726027), (80.7668595 6.9726027, 80.766862 6.9724381), (80.766862 6.9724381, 80.7668706 6.9721991), (80.7668706 6.9721991, 80.7668843 6.9720105), (80.7668843 6.9720105, 80.76690000000001 6.9717953), (80.76690000000001 6.9717953, 80.7669267 6.9717803), (80.7669267 6.9717803, 80.766947 6.9717576), (80.766947 6.9717576, 80.7669587 6.9717295), (80.7669587 6.9717295, 80.7669606 6.9716991), (

print route_geometry
MULTILINESTRING ((80.7670837 6.9738216, 80.76707500000001 6.9738283), (80.7670928 6.9738167, 80.7670837 6.9738216), (80.7670928 6.9738167, 80.7670457 6.973783), (80.7670457 6.973783, 80.7670078 6.9737515), (80.7670078 6.9737515, 80.7669736 6.9737191), (80.7669736 6.9737191, 80.7669571 6.9736939), (80.7669571 6.9736939, 80.7669453 6.9736601), (80.7669453 6.9736601, 80.76693400000001 6.973613), (80.76693400000001 6.973613, 80.7669259 6.9735561), (80.7669259 6.9735561, 80.7669059 6.9733364), (80.7669059 6.9733364, 80.76686189999999 6.9727634), (80.76686189999999 6.9727634, 80.7668595 6.9726027), (80.7668595 6.9726027, 80.766862 6.9724381), (80.766862 6.9724381, 80.7668706 6.9721991), (80.7668706 6.9721991, 80.7668843 6.9720105), (80.7668843 6.9720105, 80.76690000000001 6.9717953), (80.76690000000001 6.9717953, 80.7669267 6.9717803), (80.7669267 6.9717803, 80.766947 6.9717576), (80.766947 6.9717576, 80.7669587 6.9717295), (80.7669587 6.9717295, 80.7669606 6.9716991), (

print route_geometry
MULTILINESTRING ((80.7670837 6.9738216, 80.76707500000001 6.9738283), (80.7670928 6.9738167, 80.7670837 6.9738216), (80.7670928 6.9738167, 80.7670457 6.973783), (80.7670457 6.973783, 80.7670078 6.9737515), (80.7670078 6.9737515, 80.7669736 6.9737191), (80.7669736 6.9737191, 80.7669571 6.9736939), (80.7669571 6.9736939, 80.7669453 6.9736601), (80.7669453 6.9736601, 80.76693400000001 6.973613), (80.76693400000001 6.973613, 80.7669259 6.9735561), (80.7669259 6.9735561, 80.7669059 6.9733364), (80.7669059 6.9733364, 80.76686189999999 6.9727634), (80.76686189999999 6.9727634, 80.7668595 6.9726027), (80.7668595 6.9726027, 80.766862 6.9724381), (80.766862 6.9724381, 80.7668706 6.9721991), (80.7668706 6.9721991, 80.7668843 6.9720105), (80.7668843 6.9720105, 80.76690000000001 6.9717953), (80.76690000000001 6.9717953, 80.7669267 6.9717803), (80.7669267 6.9717803, 80.766947 6.9717576), (80.766947 6.9717576, 80.7669587 6.9717295), (80.7669587 6.9717295, 80.7669606 6.9716991), (

print route_geometry
MULTILINESTRING ((80.7670837 6.9738216, 80.76707500000001 6.9738283), (80.7670928 6.9738167, 80.7670837 6.9738216), (80.7670928 6.9738167, 80.7670457 6.973783), (80.7670457 6.973783, 80.7670078 6.9737515), (80.7670078 6.9737515, 80.7669736 6.9737191), (80.7669736 6.9737191, 80.7669571 6.9736939), (80.7669571 6.9736939, 80.7669453 6.9736601), (80.7669453 6.9736601, 80.76693400000001 6.973613), (80.76693400000001 6.973613, 80.7669259 6.9735561), (80.7669259 6.9735561, 80.7669059 6.9733364), (80.7669059 6.9733364, 80.76686189999999 6.9727634), (80.76686189999999 6.9727634, 80.7668595 6.9726027), (80.7668595 6.9726027, 80.766862 6.9724381), (80.766862 6.9724381, 80.7668706 6.9721991), (80.7668706 6.9721991, 80.7668843 6.9720105), (80.7668843 6.9720105, 80.76690000000001 6.9717953), (80.76690000000001 6.9717953, 80.7669267 6.9717803), (80.7669267 6.9717803, 80.766947 6.9717576), (80.766947 6.9717576, 80.7669587 6.9717295), (80.7669587 6.9717295, 80.7669606 6.9716991), (

print route_geometry
MULTILINESTRING ((80.7670837 6.9738216, 80.76707500000001 6.9738283), (80.7670928 6.9738167, 80.7670837 6.9738216), (80.7670928 6.9738167, 80.7670457 6.973783), (80.7670457 6.973783, 80.7670078 6.9737515), (80.7670078 6.9737515, 80.7669736 6.9737191), (80.7669736 6.9737191, 80.7669571 6.9736939), (80.7669571 6.9736939, 80.7669453 6.9736601), (80.7669453 6.9736601, 80.76693400000001 6.973613), (80.76693400000001 6.973613, 80.7669259 6.9735561), (80.7669259 6.9735561, 80.7669059 6.9733364), (80.7669059 6.9733364, 80.76686189999999 6.9727634), (80.76686189999999 6.9727634, 80.7668595 6.9726027), (80.7668595 6.9726027, 80.766862 6.9724381), (80.766862 6.9724381, 80.7668706 6.9721991), (80.7668706 6.9721991, 80.7668843 6.9720105), (80.7668843 6.9720105, 80.76690000000001 6.9717953), (80.76690000000001 6.9717953, 80.7669267 6.9717803), (80.7669267 6.9717803, 80.766947 6.9717576), (80.766947 6.9717576, 80.7669587 6.9717295), (80.7669587 6.9717295, 80.7669606 6.9716991), (

In [81]:
complete_routes

[[4784044133,
  6117715989,
  246.88436721196808,
 [4784044133,
  2085208123,
  10032.738931369538,
 [4784044133,
  2078574693,
  5795.916460938929,
 [4784044133,
  1146790064,
  5595.063131734092,
 [4784044133,
  5497589950,
  2950.074791835917,
 [4784044133,
  1709670615,
  7434.484289476964,
 [4784044133,
  7083442431,
  487.7241048543604,
 [4784044133,
  5596123398,
  108.42347631157406,
 [4784044133,
  3686420776,
  1637.2084357810513,
 [4784044133,
  849219917,
  1904.1076835367949,
 [4784044133,
  3169970562,
  5568.867545875503,
 [4784044133,
  5190957535,
  4670.902359820437,
 [4784044133,
  2032265757,
  5526.001285638923,
 [4784044133,
  4796981814,
  896.8536045764732,
 [4784044133,
  247141019,
  879.9376132951525,
 [4784044133,
  3385797326,
  3245.6044597307505,
 [4784044133,
  2055187157,
  2648.5007089037003,
 [4784044133,
  4483212105,
  90.38424543557855,
 [4784044133,
  198507384,
  287.03449705024354,
 [4784044133,
  3169835909,
  7229.622016587151,
 [4784044133,
 

In [82]:
complete_routes_df = pd.DataFrame(complete_routes, columns = ['origin','destination','time','geometry'])

In [83]:
complete_routes_df

origin  destination          time  \
0   4784044133   6117715989    246.884367   
1   4784044133   2085208123  10032.738931   
2   4784044133   2078574693   5795.916461   
3   4784044133   1146790064   5595.063132   
4   4784044133   5497589950   2950.074792   
5   4784044133   1709670615   7434.484289   
6   4784044133   7083442431    487.724105   
7   4784044133   5596123398    108.423476   
8   4784044133   3686420776   1637.208436   
9   4784044133    849219917   1904.107684   
10  4784044133   3169970562   5568.867546   
11  4784044133   5190957535   4670.902360   
12  4784044133   2032265757   5526.001286   
13  4784044133   4796981814    896.853605   
14  4784044133    247141019    879.937613   
15  4784044133   3385797326   3245.604460   
16  4784044133   2055187157   2648.500709   
17  4784044133   4483212105     90.384245   
18  4784044133    198507384    287.034497   
19  4784044133   3169835909   7229.622017   
20  4784044133   2035852184    397.318011   
21  4784044133   2032266220   9673.908524   
22  4784044133   2078542843   5606.326459   
23  4784044133    198476854    229.433278   
24  4784044133   2078542962   5500.966762   
25  4784044133   4342594760   3726.127940   
26  4784044133   3301905899   5532.948146   
27  4784044133    198553180    432.959124   
28  4784044133   2408066657   1479.318821   
29  4784044133   3615147754   8967.031034   
30  4784044133   1713880855   5902.910295   
31  4784044133   5497589553   2800.297799   
32  4784044133   2057039735   5480.234495   
33  4784044133   2057039753   5469.468574   
34  4784044133     77682630     25.618408   

                                             geometry  
0   (LINESTRING (80.7670837 6.9738216, 80.76707500...  
1   (LINESTRING (80.7670837 6.9738216, 80.76707500...  
2   (LINESTRING (80.7670837 6.9738216, 80.76707500...  
3   (LINESTRING (80.7670837 6.9738216, 80.76707500...  
4   (LINESTRING (80.7670837 6.9738216, 80.76707500...  
5   (LINESTRING (80.7670837 6.9738216, 80.76707500...  
6   (LINESTRING (80.7670837 6.9738216, 80.76707500...  
7   (LINESTRING (80.7670837 6.9738216, 80.76707500...  
8   (LINESTRING (80.7670837 6.9738216, 80.76707500...  
9   (LINESTRING (80.7670837 6.9738216, 80.76707500...  
10  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
11  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
12  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
13  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
14  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
15  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
16  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
17  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
18  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
19  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
20  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
21  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
22  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
23  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
24  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
25  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
26  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
27  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
28  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
29  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
30  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
31  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
32  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
33  (LINESTRING (80.7670837 6.9738216, 80.76707500...  
34  (LINESTRING (80.7670837 6.9738216, 80.76707500...

In [84]:
complete_routes_gdf = gpd.GeoDataFrame(complete_routes_df, crs = 'epsg:4326')

In [85]:
complete_routes_gdf

origin  destination          time  \
0   4784044133   6117715989    246.884367   
1   4784044133   2085208123  10032.738931   
2   4784044133   2078574693   5795.916461   
3   4784044133   1146790064   5595.063132   
4   4784044133   5497589950   2950.074792   
5   4784044133   1709670615   7434.484289   
6   4784044133   7083442431    487.724105   
7   4784044133   5596123398    108.423476   
8   4784044133   3686420776   1637.208436   
9   4784044133    849219917   1904.107684   
10  4784044133   3169970562   5568.867546   
11  4784044133   5190957535   4670.902360   
12  4784044133   2032265757   5526.001286   
13  4784044133   4796981814    896.853605   
14  4784044133    247141019    879.937613   
15  4784044133   3385797326   3245.604460   
16  4784044133   2055187157   2648.500709   
17  4784044133   4483212105     90.384245   
18  4784044133    198507384    287.034497   
19  4784044133   3169835909   7229.622017   
20  4784044133   2035852184    397.318011   
21  4784044133   2032266220   9673.908524   
22  4784044133   2078542843   5606.326459   
23  4784044133    198476854    229.433278   
24  4784044133   2078542962   5500.966762   
25  4784044133   4342594760   3726.127940   
26  4784044133   3301905899   5532.948146   
27  4784044133    198553180    432.959124   
28  4784044133   2408066657   1479.318821   
29  4784044133   3615147754   8967.031034   
30  4784044133   1713880855   5902.910295   
31  4784044133   5497589553   2800.297799   
32  4784044133   2057039735   5480.234495   
33  4784044133   2057039753   5469.468574   
34  4784044133     77682630     25.618408   

                                             geometry  
0   MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
1   MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
2   MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
3   MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
4   MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
5   MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
6   MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
7   MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
8   MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
9   MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
10  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
11  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
12  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
13  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
14  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
15  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
16  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
17  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
18  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
19  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
20  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
21  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
22  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
23  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
24  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
25  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
26  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
27  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
28  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
29  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
30  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
31  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
32  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
33  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...  
34  MULTILINESTRING ((80.76708 6.97382, 80.76708 6...

In [86]:
# export to shapefile

In [87]:
complete_edges

[[4784044133, 3819995230],
 [3819995230, 4776878438],
 [4776878438, 6720549511],
 [6720549511, 6720549512],
 [6720549512, 4790267482],
 [4790267482, 6720549510],
 [6720549510, 6720549504],
 [6720549504, 6720549509],
 [6720549509, 4776878436],
 [4776878436, 191850645],
 [191850645, 191850698],
 [191850698, 247162948],
 [247162948, 4775747483],
 [4775747483, 4775747484],
 [4775747484, 247162945],
 [247162945, 4775747485],
 [4775747485, 336184347],
 [336184347, 77682693],
 [77682693, 2829005549],
 [2829005549, 6117715995],
 [6117715995, 6117715994],
 [6117715994, 6117715999],
 [6117715999, 6117715993],
 [6117715993, 6117715992],
 [6117715992, 6117715998],
 [6117715998, 6117715991],
 [6117715991, 6117715990],
 [6117715990, 6117715997],
 [6117715997, 6117715989],
 [4784044133, 3819995230],
 [3819995230, 4776878438],
 [4776878438, 6720549511],
 [6720549511, 6720549512],
 [6720549512, 4790267482],
 [4790267482, 6720549510],
 [6720549510, 6720549504],
 [6720549504, 6720549509],
 [6720549509, 4

In [88]:
complete = pd.DataFrame(complete_edges, columns = ['o', 'd'])
complete['w'] = 1
complete_count = pd.DataFrame(complete.groupby(['o','d']).count())
complete_count.reset_index(inplace = True)
complete_count['o'] = complete_count['o'].astype(str)
complete_count['d'] = complete_count['d'].astype(str)

In [89]:
#complete_count = pd.merge(complete_count, nodes_data.loc[:,['node_id','Point']], left_on = 'o', right_on='node_id')
#complete_count = pd.merge(complete_count, nodes_data.loc[:,['node_id','Point']], left_on = 'd', right_on='node_id')
#complete_count['geometry'] = [LineString([x,y]) for x, y in zip(complete_count['Point_x'], complete_count["Point_y"])]
complete_count = complete_count.loc[:,['o','d','w']]

In [90]:
complete_count

o           d   w
0        49364661  5018474153   1
1        49364685  5018474148   1
2        49364700  5018474164   1
3        49364719  4571633797   1
4        49364756  5018474144   1
...           ...         ...  ..
21096  7095172437    49369047  18
21097  7229317182  3385797191   2
21098  7279591542   598167787   5
21099  7323225814   598167898   5
21100  7323226260   598167910   5

[21101 rows x 3 columns]

### testing 

In [66]:
OD_df

{1243386867:               2291208197   2100457519  1242787912   1895649399  1242787995  \
 1243386867  10050.216305  7627.850486  568.038849  8314.240104  232.102591   
 
              3806787750  4248172715   5580828849   3851290872  4579338537  \
 1243386867  1622.532349  164.500294  5897.514957  3067.214478  8049.56954   
 
             ...   1676588668   3350242971   1685802748   1723379544  \
 1243386867  ...  9953.941107  15283.23918  3490.102543  1613.940152   
 
             2477387622  1775835028   3165939618   5965445027    1675585459  \
 1243386867  9902.33526  540.556013  6677.291317  6219.852061  10018.693219   
 
              1675585534  
 1243386867  9988.043033  
 
 [1 rows x 36 columns],
 1727494683:              4784988278  3208652929   6988599546   2833357077   6181355836  \
 1727494683  3914.615286  6070.48506  7779.166397  7680.141252  3649.504852   
 
              3213648201   2646372818   5441882639   5035668064   2051261052  \
 1727494683  3044.576043  7569.8

In [68]:
OD_df[1243386867]

2291208197   2100457519  1242787912   1895649399  1242787995  \
1243386867  10050.216305  7627.850486  568.038849  8314.240104  232.102591   

             3806787750  4248172715   5580828849   3851290872  4579338537  \
1243386867  1622.532349  164.500294  5897.514957  3067.214478  8049.56954   

            ...   1676588668   3350242971   1685802748   1723379544  \
1243386867  ...  9953.941107  15283.23918  3490.102543  1613.940152   

            2477387622  1775835028   3165939618   5965445027    1675585459  \
1243386867  9902.33526  540.556013  6677.291317  6219.852061  10018.693219   

             1675585534  
1243386867  9988.043033  

[1 rows x 36 columns]

In [70]:
OD_df[1243386867][OD_df[1243386867] > 500]

2291208197   2100457519  1242787912   1895649399  1242787995  \
1243386867  10050.216305  7627.850486  568.038849  8314.240104         NaN   

             3806787750  4248172715   5580828849   3851290872  4579338537  \
1243386867  1622.532349         NaN  5897.514957  3067.214478  8049.56954   

            ...   1676588668   3350242971   1685802748   1723379544  \
1243386867  ...  9953.941107  15283.23918  3490.102543  1613.940152   

            2477387622  1775835028   3165939618   5965445027    1675585459  \
1243386867  9902.33526  540.556013  6677.291317  6219.852061  10018.693219   

             1675585534  
1243386867  9988.043033  

[1 rows x 36 columns]

In [71]:
# 9999999
OD_df[1243386867][OD_df[1243386867] > 500].count()

2291208197    1
2100457519    1
1242787912    1
1895649399    1
1242787995    0
3806787750    1
4248172715    0
5580828849    1
3851290872    1
4579338537    1
1896380803    1
1884656092    1
1896380948    1
1880627748    1
6177931854    1
7076053840    1
3985464364    1
4542639194    1
4376980578    1
3805734132    1
3315891502    1
2278210866    1
3893372372    1
7025200613    1
2341660185    1
6021684779    1
1676588668    1
3350242971    1
1685802748    1
1723379544    1
2477387622    1
1775835028    1
3165939618    1
5965445027    1
1675585459    1
1675585534    1
dtype: int64

In [72]:
pd.Series.ge(OD_df[1243386867][OD_df[1243386867] > 9999998].count(), 2).value_counts()

False    36
dtype: int64

## test airports

In [73]:
airports = gpd.read_file('./origins_destinations/intl_airport.shp')

In [74]:
airports

osm_id emergencyh  aeroway operatorty source capacitype addrfull  \
0  4.197465e+09       None  helipad       None   None       None     None   
1  1.912607e+08       None     None       None   None       None     None   
2  7.479128e+08       None     None       None   None       None     None   

  emergency                             name addrcity building    POINT_X  \
0      None          Ratmalana Int'l Airport     None     None  79.885533   
1      None  Mattala Rajapaksa Int'l Airport     None     None   0.000000   
2      None             Jaffna Int'l Airport     None     None   0.000000   

    POINT_Y                  geometry  
0  6.823861  POINT (79.88553 6.82386)  
1  0.000000  POINT (81.12338 6.28615)  
2  0.000000  POINT (80.06853 9.79439)

In [75]:
airports_gdf = gn.pandana_snap_c(G, airports, source_crs = 'epsg:4326', target_crs = 'epsg:32644')

In [76]:
airports_list = list(set(airports_gdf.NN))

In [77]:
airport_OD = gn.calculate_OD(G, airports_list, destinations_list, fail_value = 9999999)

In [78]:
airport_OD_df = pd.DataFrame(airport_OD, index = airports_list, columns = destinations_list)

In [79]:
airport_OD_df

2291208197    1667080206    6991570964    6117715989  \
4075647849  24033.093498  28158.388596  26530.008215  29384.999445   
5456722972  23962.943130   2729.046989   1582.915207  16657.734032   
3261840927  18637.304574   8269.627751  10611.644448  12086.846317   

              1743126554    2100457519    1185558575    130445367   \
4075647849  23811.291059   9480.562118  27431.387833  29804.109941   
5456722972  11238.089139  24993.359934    401.104665   5274.042297   
3261840927  17745.441512  31500.712308   9320.546367   6776.161683   

              2085208123    4047450172  ...    3772792789    3772792790  \
4075647849  35097.126348  21805.720480  ...  27120.710595  27110.255784   
5456722972  14162.375077  11981.972575  ...    670.014065    680.468876   
3261840927  10405.112134  18073.755040  ...   9847.748914   9858.203725   

              1730404311    258523099     6564888541    3216934896  \
4075647849  33671.250749  17873.240241   5591.199142  25322.204140   
5456722972  11312.086677  16951.463517  23003.510557   7961.552420   
3261840927   1991.552584  18571.012278  29510.862931  14193.040409   

              1506164725    1657419767    1675585534    4621961215  
4075647849  30710.229356  12620.810646  23970.920226  26473.738556  
5456722972   6180.161711  15418.675025  23900.769858   1738.544752  
3261840927   5520.125862  21926.027399  18410.113726  10798.849008  

[3 rows x 337 columns]